In [1]:
import numpy as np
import pandas as pd
import scipy.stats as st

In [2]:
r = 0.05
delta = 0.04
sigma = 0.2

In [3]:
F = lambda x: st.norm.cdf(x, 0, 1)
print(F(-2.54))

phi = lambda x: st.norm.pdf(x, 0, 1)
print(phi(0.45))

Alpha = r - delta
Alpha_ = Alpha - sigma**2/2

0.00554262344308
0.360526962462


In [4]:
# Ingersoll-Ross model - не думаю, что надо. Это решение диф уравнения, но для данной модели не находили
# стоимость опциона
gamma = 0
a = 0
b = 0

eta = np.sqrt(b**2 + 2*gamma**2)

D = lambda t: 2*(1-np.exp(eta*(T-t))) / ((eta+b)*np.exp(eta*(T-t))+eta-b)
E = lambda t: 2*a/gamma**2*(np.log(2*eta*np.exp((b+eta)*(T-t)/2)) - \
                            np.log((b+eta)*np.exp(eta*(T-t))+eta-b))
B = lambda r,t: np.exp(E(t) + r*D(t))

In [ ]:
# Оценка стоимости колл-опциона при переменной процентной ставке (Hull-White model)
# ...

In [ ]:
#Мертон Call опцион 
def trapezoidal(f, a, b, n): 
    h = float(b - a)/n 
    result = 0.5*(f(a) + f(b)) 
    for i in range(1, n): 
    result += f(a + i*h) 
    result *= h 
    return result
    

def Call_Mert(S,B,t=0):
    T=1#год
    delta = 0.04
    K=1000#страйк
    p=S/B
    
    sigma = lambda x: #здесь функцию x как бы t
    sigma_2 = trapezoidal(sigma,t,T,10000)#сначала g1(t) вручную, потом sigma(t) через данные функции, а потом сигма^2 c чертой через интеграл
    
    H=p*np.exp(-delta*(T-t))*F((np.log(p/K)+(-delts+sigma_2/2)*(T-t))/np.sqrt(sigma_2*(T-t))) + 
    K*F((np.log(p/K)+(-delts-sigma_2/2)*(T-t))/np.sqrt(sigma_2*(T-t)))
    
    return B*H

In [ ]:
# Оценка стоимости опциона при переменной волатильности (Heston model)
# ...

In [5]:
# Оценка опционов на 2 актива с однородными обязательствами
p = 1
T = 100
delta_1 = 0.01
delta_2 = 0.02

d1 = lambda t: (np.log(p) + (Alpha_+sigma**2)*(T-t))/sigma/np.sqrt(T-t)
d2 = lambda t: (np.log(p) + Alpha_*(T-t))/sigma/np.sqrt(T-t)

# Оценка Односторонних опционов Марграбе
C_12 = lambda S1, S2, t: S1*np.exp(-delta_1*(T-t))*F(d1(t)) - S2*np.exp(-delta_2*(T-t))*F(d2(t))
C_21 = lambda S1, S2, t: -S1*np.exp(-delta_1*(T-t))*F(-d1(t)) + S2*np.exp(-delta_2*(T-t))*F(-d2(t))

# Оценка двустороннего опциона Марграбе
C_M = lambda S1, S2, t: C_12(S1, S2, t) + C_21(S1, S2, t)

# Оценка альтернативных опционов на максимум и на минимум
C_max = lambda S1, S2, t: S2*np.exp(-delta_2*(T-t)) + C_12(S1, S2, t)
C_min = lambda S1, S2, t: S1*np.exp(-delta_1*(T-t)) - C_12(S1, S2, t)

In [6]:
def J(u,a,b):
    if a != 0:
        res = -1/a * np.exp(a*u) * F((-u+b*T)/sigma / np.sqrt(T)) + \
              1/a * np.exp((a*b+a**2*sigma**2/2)*T) * F((-u+(b+a*sigma**2)*T)/sigma / np.sqrt(T))
    if a == 0:
        res = (-u+b*T)*F((-u+b*T)/sigma / np.sqrt(T)) + \
              sigma*np.sqrt(T)*phi((-u+b*T)/sigma / np.sqrt(T))
    return res

# Оценка русского колл-опциона
def C_russ(S, L, t=0):
    x_K = np.log(L/K)
    x_L = np.log(L/S)
    if L <= K:
        res = np.exp(-r*T)*S*(J(x_K,1,Alpha_) + J(x_K, 2*Alpha/sigma**2, -Alpha_))
    if L > K:
        res = np.exp(-r*T)*(L-K+S*(J(x_L,1,Alpha_) + J(x_L, 2*Alpha/sigma**2, -Alpha_)))
    return res

# Оценка пут-опциона look-back
def P_look(S, L, t=0):
    x_L = np.log(L/S)
    return(np.exp(-r*T)*(L+S*(J(x_L,1,Alpha_) + J(x_L, 2*Alpha/sigma**2, -Alpha_))-S*np.exp(Alpha*T)))

# Оценка русского пут-опциона
def P_russ(S, L, t=0):
    x_K = np.log(L/K)
    x_L = np.log(L/S)
    if L > K:
        res = np.exp(-r*T)*S*(J(-x_K,-1,-Alpha_) + J(-x_K, -2*Alpha/sigma**2, Alpha_))
    if L <= K:
        res = np.exp(-r*T)*(K-L+S*(J(-x_L,-1,-Alpha_) + J(-x_L, -2*Alpha/sigma**2, Alpha_)))
    return res

# Оценка колл-опциона look-back
def C_look(S, L, t=0):
    x_L = np.log(L/S)
    return(np.exp(-r*T)*(np.exp(Alpha*T)*S - L + S*(J(-x_L,-1,-Alpha_) + J(-x_L, -2*Alpha/sigma**2, Alpha_))))

In [ ]:
#Пуассон
def Puasson():
    t=0
    T = 0.5
    r=0.05
    n=3#количество первых слагаемых в бесконечной сумме
    K=1000#strike
    m=20#Мат ожидание Qi
    sigma_q_2 = 100#дисперсия Qi
    alfa = 10
    sigma_2 = 100 # станд откл цены в квадрате
    S=100#начальная стоимость акции
    lambd = 3 #параметр распределния Пуассона
    delta = 0.04
    J=3#Вычисляем сами из соображения Еe^Qi=J+1
    
    sigma_n_2 = sigma**2+n*sigma_q_2/T
    alfa_mod=alfa - sigma_2/2
    
    p = lambda t,n: np.exp(-lambd*t)*np.power(lambd*t,n)/np.math.factorial(n)#А мы че, в t=0??? тогда здеь все вырождено, спосить у Морозова!!
    #И если что по необходимости исправить T на T-t в дальнейшем
    
    #С учетом того, что n>=1, при n=0 обычный Б-Ш
    Otvet = p(t,0)*(S*np.exp(-delta*(T))*F((np.log(S/K)+(alpha_mod+sigma_2)*(T))/(np.sqrt(sigma_2*(T))))-
                   K*np.exp(-r*(T))*F((np.log(S/K)+alpha_mod*(T))/(np.sqrt(sigma_2*(T)))))
    
    for w in range(1,n+1):
        Otvet += p(t,w)*(S*np.exp(-delta*(T))*F((np.log(S/K)+(alpha_mod-lambd*J)*(T)+m*w+sigma_n_2*T)/(np.sqrt(sigma_n_2*(T))))-
                        K*np.exp(-r*(T))*F((np.log(S/K)+(alpha_mod-lambd*J)*(T)+w*m)/(np.sqrt(sigma_n_2*(T)))))
    return Otvet